In [90]:
import pandas as pd
import re, nltk, random, os, json
import numpy as np
from nltk.corpus import stopwords
from rank_bm25 import BM25Okapi, BM25L, BM25Plus

In [112]:
from transformers import BertTokenizer, BertForQuestionAnswering
import torch
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
model = DST_SPAN.from_pretrained('bert-base-uncased')

In [222]:
def get_cls_vector(value):
    inputs = tokenizer(value, return_tensors="pt")
    CLS = model.bert(**inputs)
    return CLS[0][0][0].detach().numpy()
candidate_values = []
target_value = get_cls_vector(ontology['hotel-price range'][0])
for value in ontology['hotel-price range'][1:]:
    CLS = get_cls_vector(value)
    candidate_values.append(CLS)
candidate_values.append([0]*768)
torch.tensor(batch)

tensor([[0, 1, 2]])
tensor([[0, 1, 2, 3, 4, 5, 6]])
tensor([[0, 1, 2]])
tensor([[0, 1, 2]])


tensor([[ 0.2959,  0.2692, -0.0319,  ...,  0.0770,  0.2588,  0.3608],
        [-0.7963, -0.0198, -0.6396,  ...,  0.1912,  0.1345,  0.3741],
        [-0.1936,  0.2094, -0.1374,  ..., -0.0857, -0.0335,  0.0727]])

In [229]:
inputs = tokenizer("I would like to book a cheap hotel room on Monday", return_tensors="pt")
start_positions = torch.tensor([-1])
end_positions = torch.tensor([-1])
slot_positions = torch.tensor([2])

slot_value_targets = torch.tensor([target_value,target_value])
slot_value_candidates = torch.tensor([candidate_values,candidate_values])

# outputs = model(**inputs, slot_value_targets=slot_value_targets, slot_value_candidates=slot_value_candidates, start_positions=start_positions, end_positions=end_positions, slot_positions=slot_positions)

In [182]:
slot2idx = {slot:idx for idx, slot in enumerate(ontology.keys())}

In [2]:
# Simple Transformer Experiment
from simpletransformers.question_answering import QuestionAnsweringModel
import json
import os
import logging


logging.basicConfig(level=logging.INFO)
transformers_logger = logging.getLogger("transformers")
transformers_logger.setLevel(logging.WARNING)

# Create the QuestionAnsweringModel
model = QuestionAnsweringModel('bert', 'bert-base-uncased', use_cuda=False, args={'reprocess_input_data': True, 'overwrite_output_dir': True, 'use_cuda': False})

/Users/jarana/anaconda3/envs/torch1/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/Users/jarana/anaconda3/envs/torch1/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/Users/jarana/anaconda3/envs/torch1/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:518: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/Users/jarana/anaconda3/envs/torch1/lib/pyt

In [2]:
import glob, re, math

def camel_case_split(str): 
    words = [[str[0]]] 
    for c in str[1:]: 
        if words[-1][-1].islower() and c.isupper(): 
            words.append(list(c)) 
        else: 
            words[-1].append(c) 

    return " ".join([i.lower() for i in [''.join(word) for word in words]])    

def cleanhtml(raw_html):
    cleanr = re.compile('<.*?>')
    cleantext = re.sub(cleanr, '', raw_html)
    return cleantext.lower()

def simplifyDomainName(oldName):
    special = {"buse": "bus", "rentalcar": "rent car", "ridesharing": "taxi", "messaging": "message"}
    newName = oldName.split("_")[0].lower()
    if newName[-1] == "s":
        newName = newName[:-1]
    if newName in special:
        newName = special[newName]
    return newName

In [84]:
import pandas as pd
schema = pd.read_json("data/dstc8-schema-guided-dialogue/train/schema.json")
schema = pd.concat([schema, pd.read_json("data/dstc8-schema-guided-dialogue/dev/schema.json")])
schema = pd.concat([schema, pd.read_json("data/dstc8-schema-guided-dialogue/test/schema.json")])

In [37]:
import glob, os
# generate dstc8-schema-guided-dialogue
# Train and Test set
def read_dst_file(path_to_json):
    dst = pd.DataFrame()
    json_pattern = os.path.join(path_to_json,'dialogues_*.json')
    file_list = glob.glob(json_pattern)

    for file in file_list:
        tmp = pd.read_json(file)
        dst = dst.append(tmp)
    return dst
dst_train = read_dst_file('data/dstc8-schema-guided-dialogue/train/')
dst_valid = read_dst_file('data/dstc8-schema-guided-dialogue/dev/')
dst_test = read_dst_file('data/dstc8-schema-guided-dialogue/test/')

In [192]:
wdc = pd.read_csv("data/web-data-common/wdc1M", sep="\t", encoding='utf-8', engine='python', error_bad_lines=False, names=["entityType", "website", "property", "value"])
wdc = wdc.dropna()
wdc = wdc.drop_duplicates()
wdc = wdc[~wdc.value.str.contains("https")]
wdc = wdc[~wdc.property.str.contains('|'.join(['width', 'height','ownershipFundingInfo', 'description', 'keywords', 'caption', 'query-input', 'name', 'headline', 'url', 'sameAs', 'target', 'actionPlatform']))]

In [123]:
tmp = wdc[wdc.entityType.isin(["Hotel", "Restaurant", "Place", "City", "Hospital"])]

In [125]:
tmp

entityType                                            website  \
277802         City        https://www.kombo.co/en/bus-Karlsruhe-Genoa   
277803         City        https://www.kombo.co/en/bus-Karlsruhe-Genoa   
277804         City        https://www.kombo.co/en/bus-Karlsruhe-Genoa   
277805         City        https://www.kombo.co/en/bus-Karlsruhe-Genoa   
277806         City        https://www.kombo.co/en/bus-Karlsruhe-Genoa   
...             ...                                                ...   
2516191  Restaurant  https://www.marriott.fr/hotels/hotel-photos/qq...   
2516192  Restaurant  https://www.marriott.fr/hotels/hotel-photos/qq...   
2516193  Restaurant  https://www.marriott.fr/hotels/hotel-photos/qq...   
2516195  Restaurant  https://www.marriott.fr/hotels/hotel-photos/qq...   
2516196  Restaurant  https://www.marriott.fr/hotels/hotel-photos/qq...   

                property                      value  
277802             price                      15.99  
277803     priceCurrency                        EUR  
277804      availability  http://schema.org/InStock  
277805    addressCountry                         DE  
277806          latitude                   4.9014E1  
...                  ...                        ...  
2516191        telephone            +44 1904 701000  
2516192        faxnumber            +44 1904 702308  
2516193  addressLocality                       York  
2516195   addressCountry                Royaume-Uni  
2516196       postalCode                   YO24 1QQ  

[280704 rows x 4 columns]

In [126]:
tmp[['entityType', 'property']].drop

entityType         property
277802         City            price
277803         City    priceCurrency
277804         City     availability
277805         City   addressCountry
277806         City         latitude
...             ...              ...
2516191  Restaurant        telephone
2516192  Restaurant        faxnumber
2516193  Restaurant  addressLocality
2516195  Restaurant   addressCountry
2516196  Restaurant       postalCode

[280704 rows x 2 columns]

In [42]:
import random
sample_wdc = wdc[wdc.website.isin(random.sample(wdc.website.unique().tolist(), 100))]

In [146]:
tmp = pd.read_csv("data/schema.org/schema-properties.csv")
prop2desc = pd.Series(tmp.comment.values,index=tmp.label).to_dict()

In [46]:
def generate_wdc_data(wdc, filename):
    train_data = []
    qid = 0
    for idx, grp in wdc.groupby("website"):
        try:
            context = " ".join(grp['value'].tolist())
            qas = []
            for i, row in grp.iterrows():
                if row['property'] in prop2desc:
                    qas.append({'id': "schema.org-" + str(qid), 'is_impossible': False, 'question': prop2desc[row['property']], 'answers': [{'text': row['value'], 'answer_start': context.find(row['value'])}]})
                    qid += 1
            train_data.append({'context': context, 'qas' : qas})
        except:
            continue
    # Save as a JSON file
    os.makedirs('data', exist_ok=True)
    with open('data/%s.json' % filename, 'w') as f:
        json.dump(train_data, f)
#     return train_data
generate_wdc_data(sample_wdc, "wdc")
# Train the model with JSON file
# model.train_model('data/wdc.json')

In [47]:
model.train_model('data/wdc.json')

INFO:simpletransformers.question_answering.question_answering_model: Converting to features started.
  0%|          | 0/677 [00:00<?, ?it/s]INFO:simpletransformers.question_answering.question_answering_utils:*** Example ***
INFO:simpletransformers.question_answering.question_answering_utils:unique_id: 1000000000
INFO:simpletransformers.question_answering.question_answering_utils:example_index: 0
INFO:simpletransformers.question_answering.question_answering_utils:doc_span_index: 0
INFO:simpletransformers.question_answering.question_answering_utils:tokens: [CLS] [UNK] title of the job . [SEP] [UNK] / in [UNK] das [UNK] 344 ##9 ##7 [UNK] [SEP]
INFO:simpletransformers.question_answering.question_answering_utils:token_to_orig_map: 8:0 9:0 10:0 11:1 12:2 13:3 14:4 15:4 16:4 17:5
INFO:simpletransformers.question_answering.question_answering_utils:token_is_max_context: 8:True 9:True 10:True 11:True 12:True 13:True 14:True 15:True 16:True 17:True
INFO:simpletransformers.question_answering.quest

INFO:simpletransformers.question_answering.question_answering_utils:token_is_max_context: 9:True 10:True 11:True 12:True 13:True 14:True 15:True 16:True 17:True 18:True 19:True 20:True 21:True 22:True 23:True 24:True 25:True 26:True 27:True 28:True 29:True 30:True 31:True 32:True 33:True 34:True 35:True 36:True 37:True 38:True 39:True 40:True 41:True 42:True 43:True 44:True 45:True 46:True 47:True 48:True 49:True 50:True 51:True 52:True 53:True 54:True 55:True 56:True 57:True 58:True 59:True 60:True 61:True 62:True 63:True 64:True 65:True 66:True 67:True 68:True 69:True 70:True 71:True 72:True 73:True 74:True 75:True 76:True 77:True 78:True 79:True 80:True 81:True 82:True 83:True 84:True 85:True 86:True 87:True 88:True 89:True 90:True 91:True 92:True 93:True 94:True 95:True 96:True 97:True 98:True 99:True 100:True 101:True 102:True 103:True 104:True 105:True 106:True 107:True 108:True 109:True 110:True 111:True 112:True 113:True 114:True 115:True 116:True 117:True 118:True 119:True 120

INFO:simpletransformers.question_answering.question_answering_utils:token_is_max_context: 9:True 10:True 11:True 12:True 13:True 14:True 15:True 16:True 17:True 18:True 19:True 20:True 21:True 22:True 23:True 24:True 25:True 26:True 27:True 28:True 29:True 30:True 31:True 32:True 33:True 34:True 35:True 36:True 37:True 38:True 39:True 40:True 41:True 42:True 43:True 44:True 45:True 46:True 47:True 48:True 49:True 50:True 51:True 52:True 53:True 54:True 55:True 56:True 57:True 58:True 59:True 60:True 61:True 62:True 63:True 64:True 65:True 66:True 67:True 68:True 69:True 70:True 71:True 72:True 73:True 74:True 75:True 76:True 77:True
INFO:simpletransformers.question_answering.question_answering_utils:input_ids: 101 100 25304 4180 1997 2023 100 1012 102 2115 2147 2007 2122 5352 1012 100 1996 100 100 100 100 1012 100 2003 2036 1037 2204 2801 2000 6611 1996 6510 2465 2275 16106 2008 2017 2024 4083 2000 2536 3315 10906 1012 100 2064 2224 1996 100 100 2030 3046 5128 2068 2046 2189 2008 2017 

INFO:simpletransformers.question_answering.question_answering_utils:input_mask: 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:simpletransformers.question_answering.question_answering_utils:segment_ids: 0 0 0 0 0 0 0 0 0 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:simpletransformers.question_answering.question_answering_utils:start_position: 9
INFO:simpletransformers.question_answering.question_answering_utils:end_position: 67
INFO:simpletransformers.question_answering.question_answering_utils:answer: [UNK] f ##on ##lar ##ı ara ##s ##ı ##nda kate ##gor ##ile ##re [UNK] [UNK] en fa

INFO:simpletransformers.question_answering.question_answering_utils:token_to_orig_map: 9:0 10:1 11:2 12:3 13:3 14:3 15:4 16:5 17:6 18:7 19:8 20:8 21:9 22:9 23:10
INFO:simpletransformers.question_answering.question_answering_utils:token_is_max_context: 9:True 10:True 11:True 12:True 13:True 14:True 15:True 16:True 17:True 18:True 19:True 20:True 21:True 22:True 23:True
INFO:simpletransformers.question_answering.question_answering_utils:input_ids: 101 100 25304 4180 1997 2023 100 1012 102 100 100 2474 23310 4215 4648 1061 7558 19875 2139 12943 6692 100 1012 100 102 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:simpletransformers.question_answering.question_answering_utils:input_mask: 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 

...

INFO:simpletransformers.question_answering.question_answering_utils:token_to_orig_map: 48:0 49:0 50:0 51:0 52:0 53:0 54:0 55:0 56:0 57:0 58:0 59:0 60:0 61:1 62:1 63:1 64:1 65:1 66:1 67:1 68:1 69:1 70:1 71:1 72:1 73:1 74:2 75:3 76:4
INFO:simpletransformers.question_answering.question_answering_utils:token_is_max_context: 48:True 49:True 50:True 51:True 52:True 53:True 54:True 55:True 56:True 57:True 58:True 59:True 60:True 61:True 62:True 63:True 64:True 65:True 66:True 67:True 68:True 69:True 70:True 71:True 72:True 73:True 74:True 75:True 76:True
INFO:simpletransformers.question_answering.question_answering_utils:input_ids: 101 100 2707 3058 1998 2051 1997 1996 8875 1006 1999 1026 1037 17850 12879 1027 1000 8299 1024 1013 1013 4372 1012 16948 1012 8917 1013 15536 3211 1013 100 1035 6564 24096 1000 1028 100 6564 24096 3058 4289 1026 1013 1037 1028 1007 1012 102 12609 1011 5641 1011 100 1024 4002 1024 4002 1009 4002 1024 4002 12609 1011 5641 1011 100 1024 5354 1024 5354 1009 4002 1024 4

Running loss: 2.563272

/Users/jarana/anaconda3/envs/torch1/lib/python3.6/site-packages/torch/optim/lr_scheduler.py:224: UserWarning: To get the last learning rate computed by the scheduler, please use `get_last_lr()`.
  warnings.warn("To get the last learning rate computed by the scheduler, "


Running loss: 2.436590



KeyboardInterrupt: 

In [48]:
result, text = model.eval_model('data/wdc.json')

INFO:simpletransformers.question_answering.question_answering_model: Converting to features started.
  0%|          | 0/677 [00:00<?, ?it/s]INFO:simpletransformers.question_answering.question_answering_utils:*** Example ***
INFO:simpletransformers.question_answering.question_answering_utils:unique_id: 1000000000
INFO:simpletransformers.question_answering.question_answering_utils:example_index: 0
INFO:simpletransformers.question_answering.question_answering_utils:doc_span_index: 0
INFO:simpletransformers.question_answering.question_answering_utils:tokens: [CLS] [UNK] title of the job . [SEP] [UNK] / in [UNK] das [UNK] 344 ##9 ##7 [UNK] [SEP]
INFO:simpletransformers.question_answering.question_answering_utils:token_to_orig_map: 8:0 9:0 10:0 11:1 12:2 13:3 14:4 15:4 16:4 17:5
INFO:simpletransformers.question_answering.question_answering_utils:token_is_max_context: 8:True 9:True 10:True 11:True 12:True 13:True 14:True 15:True 16:True 17:True
INFO:simpletransformers.question_answering.quest

INFO:simpletransformers.question_answering.question_answering_utils:token_is_max_context: 9:True 10:True 11:True 12:True 13:True 14:True 15:True 16:True 17:True 18:True 19:True 20:True 21:True 22:True 23:True 24:True 25:True 26:True 27:True 28:True 29:True 30:True 31:True 32:True 33:True 34:True 35:True 36:True 37:True 38:True 39:True 40:True 41:True 42:True 43:True 44:True 45:True 46:True 47:True 48:True 49:True 50:True 51:True 52:True 53:True 54:True 55:True 56:True 57:True 58:True 59:True 60:True 61:True 62:True 63:True 64:True 65:True 66:True 67:True 68:True 69:True 70:True 71:True 72:True 73:True 74:True 75:True 76:True 77:True 78:True 79:True 80:True 81:True 82:True 83:True 84:True 85:True 86:True 87:True 88:True 89:True 90:True 91:True 92:True 93:True 94:True 95:True 96:True 97:True 98:True 99:True 100:True 101:True 102:True 103:True 104:True 105:True 106:True 107:True 108:True 109:True 110:True 111:True 112:True 113:True 114:True 115:True 116:True 117:True 118:True 119:True 120

INFO:simpletransformers.question_answering.question_answering_utils:token_is_max_context: 9:True 10:True 11:True 12:True 13:True 14:True 15:True 16:True 17:True 18:True 19:True 20:True 21:True 22:True 23:True 24:True 25:True 26:True 27:True 28:True 29:True 30:True 31:True 32:True 33:True 34:True 35:True 36:True 37:True 38:True 39:True 40:True 41:True 42:True 43:True 44:True 45:True 46:True 47:True 48:True 49:True 50:True 51:True 52:True 53:True 54:True 55:True 56:True 57:True 58:True 59:True 60:True 61:True 62:True 63:True 64:True 65:True 66:True 67:True 68:True 69:True 70:True 71:True 72:True 73:True 74:True 75:True 76:True 77:True
INFO:simpletransformers.question_answering.question_answering_utils:input_ids: 101 100 25304 4180 1997 2023 100 1012 102 2115 2147 2007 2122 5352 1012 100 1996 100 100 100 100 1012 100 2003 2036 1037 2204 2801 2000 6611 1996 6510 2465 2275 16106 2008 2017 2024 4083 2000 2536 3315 10906 1012 100 2064 2224 1996 100 100 2030 3046 5128 2068 2046 2189 2008 2017 

INFO:simpletransformers.question_answering.question_answering_utils:*** Example ***
INFO:simpletransformers.question_answering.question_answering_utils:unique_id: 1000000008
INFO:simpletransformers.question_answering.question_answering_utils:example_index: 5
INFO:simpletransformers.question_answering.question_answering_utils:doc_span_index: 0
INFO:simpletransformers.question_answering.question_answering_utils:tokens: [CLS] [UNK] street address . [UNK] example , 1600 [UNK] [UNK] . [SEP] [UNK] . [UNK] [UNK] [UNK] [UNK] 46 ##8 [SEP]
INFO:simpletransformers.question_answering.question_answering_utils:token_to_orig_map: 13:0 14:0 15:1 16:2 17:3 18:4 19:5 20:5
INFO:simpletransformers.question_answering.question_answering_utils:token_is_max_context: 13:True 14:True 15:True 16:True 17:True 18:True 19:True 20:True
INFO:simpletransformers.question_answering.question_answering_utils:input_ids: 101 100 2395 4769 1012 100 2742 1010 14883 100 100 1012 102 100 1012 100 100 100 100 4805 2620 102 0 0 0

INFO:simpletransformers.question_answering.question_answering_utils:token_to_orig_map: 24:0 25:1 26:2 27:3 28:3 29:3 30:3 31:4 32:4 33:5 34:5 35:5 36:5 37:6 38:7 39:8 40:9 41:9 42:9 43:10 44:11 45:12 46:12 47:12 48:13 49:14 50:14 51:14 52:14 53:14 54:15 55:15 56:15 57:15 58:15
INFO:simpletransformers.question_answering.question_answering_utils:token_is_max_context: 24:True 25:True 26:True 27:True 28:True 29:True 30:True 31:True 32:True 33:True 34:True 35:True 36:True 37:True 38:True 39:True 40:True 41:True 42:True 43:True 44:True 45:True 46:True 47:True 48:True 49:True 50:True 51:True 52:True 53:True 54:True 55:True 56:True 57:True 58:True
INFO:simpletransformers.question_answering.question_answering_utils:input_ids: 101 100 10246 1999 2029 1996 2395 4769 2003 1010 1998 2029 2003 1999 1996 2555 1012 100 2742 1010 100 100 1012 102 29255 100 6694 100 1012 1525 100 100 1523 1181 16856 1012 2410 1011 6694 100 1009 4229 2683 1016 23532 6079 2620 2620 2236 4413 1012 25604 20958 2549 2538 101

...

INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: 'help @ vitalsource . com [UNK] [UNK] [UNK] and [UNK] http : / / schema . org / [UNK] [UNK] 9781459716919 256' in 'store.help@vitalsource.com Customer Service Napoleon and Co http://schema.org/EBook English 9781459716919 256'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: 'help @ vitalsource . com [UNK] [UNK] [UNK] and [UNK] http : / / schema . org / [UNK]' in 'store.help@vitalsource.com Customer Service Napoleon and Co http://schema.org/EBook'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: 'help @ vitalsource . com [UNK] [UNK] [UNK] and [UNK] http : / / schema . org / [UNK] [UNK] 9781459716919 256 http : / / schema . org / [UNK]' in 'store.help@vitalsource.com Customer Service Napoleon and Co http://schema.org/EBook English 9781459716919 256 http://schema.org/NewCondition'
INFO:simpletransformers.question_answering

INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: 'help @ vitalsource . com [UNK]' in 'store.help@vitalsource.com Customer'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: 'http : / / schema . org / [UNK]' in 'http://schema.org/NewCondition'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: 'http : / / schema . org / [UNK] 9 . 51 [UNK]' in 'http://schema.org/NewCondition 9.51 EUR'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '[UNK]' in 'http://schema.org/NewCondition'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '[UNK] 9 . 51 [UNK]' in 'http://schema.org/NewCondition 9.51 EUR'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '[UNK]' in 'Customer'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: 'help @ v

INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: 'help @ vitalsource . com [UNK] [UNK] [UNK] and [UNK]' in 'store.help@vitalsource.com Customer Service Napoleon and Co'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: 'http : / / schema . org / [UNK] [UNK] 9781459716919 256' in 'http://schema.org/EBook English 9781459716919 256'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: 'http : / / schema . org / [UNK]' in 'http://schema.org/EBook'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: 'http : / / schema . org / [UNK] [UNK]' in 'http://schema.org/EBook English'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: 'http : / / schema . org / [UNK] [UNK] 9781459716919 256 http' in 'http://schema.org/EBook English 9781459716919 256 http://schema.org/NewCondition'
INFO:simpletransformers.question_

INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '70 . 0 [UNK]' in '70.0 USD'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: 'http : / / schema . org / [UNK] 1999 - 01 - 26 978 - 0 - 631 - 21102 - 0 70 . 0 [UNK]' in 'http://schema.org/Paperback 1999-01-26 978-0-631-21102-0 70.0 USD'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: 'http : / / schema . org / [UNK] 1999 - 01 - 26 978 - 0 - 631 - 21102 - 0 70 . 0' in 'http://schema.org/Paperback 1999-01-26 978-0-631-21102-0 70.0'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '978 - 0 - 631 - 21102 - 0 70 . 0 [UNK]' in '978-0-631-21102-0 70.0 USD'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '[UNK]' in 'USD'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: 'http : / / schema . org / [UNK] 1999 -

INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '[UNK]' in 'USD'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '978 - 0 - 631 - 21102 - 0 70 . 0 [UNK]' in '978-0-631-21102-0 70.0 USD'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: 'http : / / schema . org / [UNK] 1999 - 01 - 26 978 - 0 - 631 - 21102 - 0 70 . 0' in 'http://schema.org/Paperback 1999-01-26 978-0-631-21102-0 70.0'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '1999 - 01 - 26 978 - 0 - 631 - 21102 - 0 70 . 0 [UNK]' in '1999-01-26 978-0-631-21102-0 70.0 USD'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: 'http : / / schema . org / [UNK] 1999 - 01 - 26 978 - 0 - 631 - 21102 - 0' in 'http://schema.org/Paperback 1999-01-26 978-0-631-21102-0'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to fi

In [35]:
slot2desc = {}
for idx, row in schema.iterrows():
    service_name = row['service_name']
    for slot in row['slots']:
        name = slot['name']
        description = slot['description']
        key = service_name + " " + name
        slot2desc[key] = description

In [201]:
# schema[]
service2desc = pd.Series(schema.description.values,index=schema.service_name).to_dict()

In [283]:
pairs = {}
def generate_data(dst, filename, isBaseline=False):
    train_data = []
    qid = 0
    dst = dst
    for idx, row in dst.iterrows():
        domain_num = len(row['services'])
        dialogue_id = row['dialogue_id']
        if domain_num > 1:
            continue
#         print(domain_num)
        context = []
        print()
        for t in range(len(row.turns)):
            utterance = row.turns[t]["utterance"]
            frames = row.turns[t]['frames']
            speaker = row.turns[t]['speaker']
            current_utterance = "%s: %s" % (speaker, utterance) if not isBaseline else utterance
            context.append(current_utterance)
            print(utterance)
            for f in range(len(frames)):
                slots = frames[f]['slots']
                service = frames[f]['service']
#                 print(slots, speaker, utterance)
                if speaker == "USER" and len(slots) >= 1:
                    qas = []
                
                    for s in range(len(slots)):
                        slot_name = slots[s]['slot']
                        pairs[utterance] = utterance[slots[s]['start']: slots[s]['exclusive_end']]
                        
                        if isBaseline:
                            past_utterances = " ".join(context) if len(context) <= 1 else " ".join(context[-2:])
                        else:
                            past_utterances = " ".join(context)

                        offset = len(past_utterances) - len(utterance)
                        start, end = slots[s]['start'] + offset, slots[s]['exclusive_end'] + offset
                        key = service + " " + slot_name
                        question = slot2desc[key] if not isBaseline else service2desc[service] + " " + slot2desc[key]
                        qas.append({'id': "%d-%s-%s-t%d-f%d-s%d" % (dialogue_id, service, slot_name, t, f, s), 'is_impossible': False, 'question': question, 'answers': [{'text': past_utterances[start:end], 'answer_start': start}]})
                    train_data.append({'context': past_utterances, 'qas' : qas})
    # Save as a JSON file
#     os.makedirs('data', exist_ok=True)
#     with open('data/sgd/%s.json' % filename, 'w') as f:
#         json.dump(train_data, f)
    return train_data
x = generate_data(dst_train[:1000], "sgd-train-single", False)
# x = generate_data(dst_valid, "sgd-valid-single", False)
# x = generate_data(dst_test, "sgd-test-single", False)


I'd like to find an event.
What are you interested in, and do you have a city preference?
I'm looking for music events in NY.
I found 10 events. How does Amber RUn Brooklyn at Warsaw sound?
Do you have any on March 4th? I like rock events.
I found 4 events. What about Low at the Murmrr.
When does it start, and where is the venue located?
The event starts at 5:30 pm, the venue is located at 17 eastern parkway, brooklyn.
Could you find me something else?
The event is The Paper Kites, it is alos at the Murmrr.
That sounds good to me.
Could you help me with anything else?
I"m interested in finding dates for events.
I found the event on 1 day. The event is on next monday, the event is The Paper Kites, at the Murmrr.
Where is the venue located?
The venue is found at 17 eastern parkway, brooklyn.
When does it start?
It starts at 5:30 pm.
That sounds great to me.
Do you want me to buy you tickets?
Yes please, I'd like 4 tickets.
please confirm the following: You want 4 tickets for The Paper K

I'd like an event in Atlanta on the 12th.
The Falcons Vs Jaguars is taking place at Mercedes-Benz Stadium on March 12th at 6:30 pm.
Tell me more about this event.
The event is an American Football event.
What is the address where it is being held?
The address is 1 AMB Drive Northwest.
That sounds perfect.
Would you like me to buy tickets for the event?
No, not right now. That is all the information I need.
Okay, have a great day.

Can you help me find an event to go to?
What type of event are you looking for? Any particular city to look it?
I'm looking for a Match even around Toronto, Ontario on the 6th of March.
I found the event Blue Jays Vs Astros, which is at the Rogers Centre. It is happening next Wednesday at 8:30 pm.
Okay, that sounds good. That's all I need.
Okay, have a nice day.

I'm loooking for events around Portland, OR can you help me?
Could I intrest you in Music or Sports?
Let's go with a music related event.
There is a Bryan Adams event at the Theater Of The Clouds tom

Okay, the songs starting to play now. Enjoy your music!
Cool, thanks. That's all I needed.
Have a nice day!

I need some help finding songs to listen to.
How about No More by Disturbed from the album Evolution.
Yeah, I like that.
Do you want me to play the song?
Yes, please play it on the kitchen speaker.
I'll play No More on the kitchen speaker, is that correct?
Sorry, no. Can you play it on the speaker in the bedroom instead?
I'll play No More on the bedroom speaker, is that correct?
Yeah, that's correct. What kind of song is it?
It's a Rock song. The song has begun.
Thanks so much.
Do you need me for anything else?
No, thank you again.
Have a good rest of your day.

Would you look for some songs for me?
How about Cool Girl by Tove Lo in Lady Wood?
What is the genre?
It is Electropop.
That sounds cool. Play that song.
So you want to play Cool Girl on the TV?
Yes that is right.
I have started playing the song.
Thank you. I do not need anything else.
Have a great day.

I would like to 

Begin playing the song.
By the way, what is this song's genre?
It is considered a Pop song.
Oh, okay. Thanks.
May I help you with anything else?
No, that's all. Thanks.
Enjoy the music.

I need to find a song for a party. I'd like a song by Major Lazer from '15.
I managed to find 1 song for you by Major Lazer. The song is called Light It Up from the album Essentials. What do you think?
What kind of song is it?
The song is Moombahton.
Yes that's great.
Should I play the song?
Yes please.
I will be playing Light It Up on the TV. Is that correct?
Yes that's perfect.
Hope you enjoy the song.
Thanks! That's all I needed.
Enjoy your day.

I'd like to hear a song. I like songs in the album The Getaway.
How about Dark Necessities by Red Hot Chili Peppers from the album The Getaway?
Is that from nine years ago?
The song is from 2016.
Ah, alright, that's the one.
Would you like to hear the song?
Yes please, play it on the kitchen speaker.
So you'd like to play Dark Necessities on Kitchen speaker

In [284]:
schema

service_name                                        description  \
0       Banks_1            Manage bank accounts and transfer money   
1       Buses_1  Book bus journeys from the biggest bus network...   
2       Buses_2        Find a bus to take you to the city you want   
3    Calendar_1  Calendar service to manage personal events and...   
4      Events_1  The comprehensive portal to find and reserve s...   
..          ...                                                ...   
16   Services_1  A widely used service for finding and reservin...   
17   Services_4  Discover the right therapist for you and make ...   
18     Trains_1  Service to find and reserve train journeys bet...   
19     Travel_1  The biggest database of tourist attractions an...   
20    Weather_1       Check the weather for any place and any date   

                                                slots  \
0   [{'name': 'account_type', 'description': 'The ...   
1   [{'name': 'from_location', 'description': 'Cit...   
2   [{'name': 'origin', 'description': 'Origin cit...   
3   [{'name': 'event_date', 'description': 'Date o...   
4   [{'name': 'category', 'description': 'Type of ...   
..                                                ...   
16  [{'name': 'stylist_name', 'description': 'Name...   
17  [{'name': 'therapist_name', 'description': 'Na...   
18  [{'name': 'from', 'description': 'Starting cit...   
19  [{'name': 'location', 'description': 'City or ...   
20  [{'name': 'precipitation', 'description': 'The...   

                                              intents  
0   [{'name': 'CheckBalance', 'description': 'Chec...  
1   [{'name': 'FindBus', 'description': 'Find a bu...  
2   [{'name': 'FindBus', 'description': 'Find a bu...  
3   [{'name': 'GetEvents', 'description': 'Get lis...  
4   [{'name': 'FindEvents', 'description': 'Find e...  
..                                                ...  
16  [{'name': 'BookAppointment', 'description': 'B...  
17  [{'name': 'BookAppointment', 'description': 'M...  
18  [{'name': 'GetTrainTickets', 'description': 'R...  
19  [{'name': 'FindAttractions', 'description': 'B...  
20  [{'name': 'GetWeather', 'description': 'Get th...  

[64 rows x 4 columns]

In [61]:
# Train the model with JSON file
model.train_model('data/sgd-test-all.json')

INFO:simpletransformers.question_answering.question_answering_model: Converting to features started.
  0%|          | 0/21 [00:00<?, ?it/s]INFO:simpletransformers.question_answering.question_answering_utils:*** Example ***
INFO:simpletransformers.question_answering.question_answering_utils:unique_id: 1000000000
INFO:simpletransformers.question_answering.question_answering_utils:example_index: 0
INFO:simpletransformers.question_answering.question_answering_utils:doc_span_index: 0
INFO:simpletransformers.question_answering.question_answering_utils:tokens: [CLS] [UNK] of the house [SEP] [UNK] : [UNK] me a house to rent . [UNK] : [UNK] city please ? [UNK] : [UNK] ' m going to [UNK] . [SEP]
INFO:simpletransformers.question_answering.question_answering_utils:token_to_orig_map: 6:0 7:0 8:1 9:2 10:3 11:4 12:5 13:6 14:6 15:7 16:7 17:8 18:9 19:10 20:10 21:11 22:11 23:12 24:12 25:12 26:13 27:14 28:15 29:15
INFO:simpletransformers.question_answering.question_answering_utils:token_is_max_context: 6

INFO:simpletransformers.question_answering.question_answering_utils:token_to_orig_map: 7:0 8:0 9:1 10:2 11:3 12:4 13:5 14:6 15:6 16:7 17:7 18:8 19:9 20:10 21:11 22:12 23:13 24:13 25:14 26:14 27:15 28:15 29:15 30:16 31:17 32:18 33:18 34:19 35:19 36:20 37:21 38:22 39:23 40:23 41:24 42:25 43:26 44:27 45:28 46:28 47:28 48:29 49:29 50:30 51:30 52:31 53:32 54:33 55:34 56:35 57:36 58:37 59:38 60:39 61:39 62:39 63:40 64:41 65:42 66:42
INFO:simpletransformers.question_answering.question_answering_utils:token_is_max_context: 7:True 8:True 9:True 10:True 11:True 12:True 13:True 14:True 15:True 16:True 17:True 18:True 19:True 20:True 21:True 22:True 23:True 24:True 25:True 26:True 27:True 28:True 29:True 30:True 31:True 32:True 33:True 34:True 35:True 36:True 37:True 38:True 39:True 40:True 41:True 42:True 43:True 44:True 45:True 46:True 47:True 48:True 49:True 50:True 51:True 52:True 53:True 54:True 55:True 56:True 57:True 58:True 59:True 60:True 61:True 62:True 63:True 64:True 65:True 66:True
IN

INFO:simpletransformers.question_answering.question_answering_utils:token_to_orig_map: 7:0 8:0 9:1 10:2 11:3 12:4 13:5 14:6 15:7 16:8 17:9 18:10 19:10 20:11 21:11 22:12 23:13 24:13 25:14 26:15 27:16 28:17 29:18 30:19 31:20 32:21 33:22 34:22 35:23 36:23 37:24 38:25 39:26 40:27 41:28 42:29 43:30 44:31 45:31 46:32 47:32 48:33 49:33 50:34 51:34 52:34 53:35 54:36 55:37 56:38 57:39 58:40 59:41 60:42 61:42 62:43 63:44 64:45 65:46 66:47 67:48 68:49 69:50 70:50 71:50 72:51 73:51 74:52 75:53 76:54 77:55 78:56 79:57 80:58 81:58 82:59 83:60 84:61 85:62 86:63 87:64 88:64 89:64 90:65 91:65 92:66 93:66 94:67 95:68 96:69 97:70 98:71 99:72 100:73 101:74 102:75 103:76 104:77 105:78 106:78 107:78 108:79 109:80 110:80
INFO:simpletransformers.question_answering.question_answering_utils:token_is_max_context: 7:True 8:True 9:True 10:True 11:True 12:True 13:True 14:True 15:True 16:True 17:True 18:True 19:True 20:True 21:True 22:True 23:True 24:True 25:True 26:True 27:True 28:True 29:True 30:True 31:True 32:Tr

INFO:simpletransformers.question_answering.question_answering_utils:answer: [UNK] - town
INFO:simpletransformers.question_answering.question_answering_utils:*** Example ***
INFO:simpletransformers.question_answering.question_answering_utils:unique_id: 1000000009
INFO:simpletransformers.question_answering.question_answering_utils:example_index: 9
INFO:simpletransformers.question_answering.question_answering_utils:doc_span_index: 0
INFO:simpletransformers.question_answering.question_answering_utils:tokens: [CLS] [UNK] rating of the house [SEP] [UNK] : [UNK] , [UNK] need to find a house where [UNK] can stay . [UNK] : [UNK] what city please ? [UNK] : [UNK] city [UNK] ' m going to is [UNK] - town . [UNK] : [UNK] have 10 possible options for you . [UNK] about 1 [UNK] [UNK] [UNK] , which is a house with a rating of 4 . 4 . [UNK] : [UNK] you look for some with a rating of 4 . 5 or more ? [SEP]
INFO:simpletransformers.question_answering.question_answering_utils:token_to_orig_map: 7:0 8:0 9:1 10

INFO:simpletransformers.question_answering.question_answering_utils:input_ids: 101 100 3058 2005 1996 11079 2030 2000 2424 1996 2160 102 100 1024 100 2572 2559 2005 1037 2160 2000 2994 1012 100 1024 100 2003 6871 2103 2005 1996 2160 1029 100 1024 100 2572 2559 2005 1037 2160 1999 100 1010 100 1012 100 1024 100 2179 2184 3506 2029 2017 2453 2066 1012 100 2055 1037 3835 2160 2007 1018 1012 1019 5790 2284 1999 1015 100 100 1010 9683 2692 2620 1029 100 1024 100 2160 4165 2307 2000 2033 1012 100 1024 100 2017 2215 2033 2000 2191 1037 11079 2005 2023 2160 1029 100 1024 100 1010 100 2191 1037 11079 2005 1018 2111 1012 100 1024 100 2003 2115 3058 1997 4638 2041 1029 100 1024 100 4638 1999 102
INFO:simpletransformers.question_answering.question_answering_utils:input_mask: 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 

...

INFO:simpletransformers.question_answering.question_answering_utils:input_mask: 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1
INFO:simpletransformers.question_answering.question_answering_utils:segment_ids: 0 0 0 0 0 0 0 0 0 0 0 0 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1
INFO:simpletransformers.question_answering.question_answering_utils:impossible example
INFO:simpletransformers.question_answering.question_answering_utils:*** Example ***
INFO:simpletransformers.question_answering.question_answering_utils:unique_id: 1000000021
INFO:simpletransformers.question_answering.question_answering_util

INFO:simpletransformers.question_answering.question_answering_utils:input_mask: 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:simpletransformers.question_answering.question_answering_utils:segment_ids: 0 0 0 0 0 0 0 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:simpletransformers.question_answering.question_answering_utils:start_position: 80
INFO:simpletransformers.question_answering.question_answering_utils:end_position: 82
INFO:simpletransformers.question_answering.question_answering_utils:answer: 4 . 5
 90%|█████████ | 19/21 [00:00<00:00, 90.16it/s] INFO:simpletransformers.q

INFO:simpletransformers.question_answering.question_answering_utils:segment_ids: 0 0 0 0 0 0 0 0 0 0 0 0 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:simpletransformers.question_answering.question_answering_utils:start_position: 81
INFO:simpletransformers.question_answering.question_answering_utils:end_position: 84
INFO:simpletransformers.question_answering.question_answering_utils:answer: 12th of this month
100%|██████████| 21/21 [00:00<00:00, 74.90it/s]


Running loss: 0.629622



INFO:simpletransformers.question_answering.question_answering_model: Training of distilbert model complete. Saved to outputs/.


In [79]:
result, text = model.eval_model('data/sgd-test-all.json')

INFO:simpletransformers.question_answering.question_answering_model: Converting to features started.
  0%|          | 0/295 [00:00<?, ?it/s]INFO:simpletransformers.question_answering.question_answering_utils:*** Example ***
INFO:simpletransformers.question_answering.question_answering_utils:unique_id: 1000000000
INFO:simpletransformers.question_answering.question_answering_utils:example_index: 0
INFO:simpletransformers.question_answering.question_answering_utils:doc_span_index: 0
INFO:simpletransformers.question_answering.question_answering_utils:tokens: [CLS] [UNK] of the house [SEP] [UNK] : [UNK] me a house to rent . [UNK] : [UNK] city please ? [UNK] : [UNK] ' m going to [UNK] . [SEP]
INFO:simpletransformers.question_answering.question_answering_utils:token_to_orig_map: 6:0 7:0 8:1 9:2 10:3 11:4 12:5 13:6 14:6 15:7 16:7 17:8 18:9 19:10 20:10 21:11 22:11 23:12 24:12 25:12 26:13 27:14 28:15 29:15
INFO:simpletransformers.question_answering.question_answering_utils:token_is_max_context: 

INFO:simpletransformers.question_answering.question_answering_utils:input_ids: 101 100 5790 1997 1996 2160 102 100 1024 100 2342 2000 9278 1037 2188 1012 100 1024 100 2103 2024 2017 8932 2000 1029 100 1024 100 1005 1049 2183 2000 100 1012 100 1024 100 2031 2184 7047 1012 1015 100 100 2038 1018 1012 1017 5790 1012 100 1024 100 2060 7047 2079 2017 2031 2007 1037 1018 1012 1014 2030 3020 5790 1029 102 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:simpletransformers.question_answering.question_answering_utils:input_mask: 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:simpletransformers.question_answering.question_answering_utils:segment_ids: 0 0 0 0 0 0 0 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1

INFO:simpletransformers.question_answering.question_answering_utils:input_ids: 101 100 5790 1997 1996 2160 102 100 1024 100 2572 2747 2559 2005 1037 2160 2000 2994 1999 1012 100 1024 100 3291 1010 2064 2017 2425 2033 2029 2103 2000 3945 1999 1029 100 1024 100 2097 2022 2635 1037 10885 2000 100 1012 100 1024 100 1010 100 1005 2310 2179 2184 3506 1999 1996 2181 2005 2017 1012 100 2003 1037 3835 2160 6758 2012 1018 1012 1015 3340 1010 2009 2003 2284 2012 1015 100 100 1010 100 100 100 100 100 17405 2509 1010 100 1012 100 1024 100 2045 2151 2060 3506 1999 1996 2181 6758 2012 2560 1018 1012 1014 2030 3020 1029 102 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:simpletransformers.question_answering.question_answering_utils:input_mask: 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:simpletrans

INFO:simpletransformers.question_answering.question_answering_utils:input_mask: 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:simpletransformers.question_answering.question_answering_utils:segment_ids: 0 0 0 0 0 0 0 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:simpletransformers.question_answering.question_answering_utils:*** Example ***
INFO:simpletransformers.question_answering.question_answering_utils:unique_id: 1000000010
INFO:simpletransformers.question_answering.question_answering_utils:example_index: 10
INFO:simpletransformers.question_answering.question_answering_utils

INFO:simpletransformers.question_answering.question_answering_utils:input_mask: 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:simpletransformers.question_answering.question_answering_utils:segment_ids: 0 0 0 0 0 0 0 0 0 0 0 0 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
  4%|▍         | 12/295 [00:00<00:02, 104.16it/s]INFO:simpletransformers.question_answering.question_answering_utils:*** Example ***
INFO:simpletransformers.question_answering.question_answering_utils:unique_id: 1000000013
INFO:simpletransformers.question_answering.question_answering_utils:example_index: 12
INFO:simpletransfo

...

INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: 'baths would you like ? [UNK] : [UNK] ' m looking to buy a house with three baths in [UNK] . [UNK] : [UNK] [UNK] , a very good property located at 135 [UNK] [UNK] is available for $ 3 , 700 , 000 . [UNK] : [UNK] sounds good to me . [UNK]' in 'baths would you like? USER: I'm looking to buy a house with three baths in Napa. SYSTEM: Bristol Apartments, a very good property located at 135 Freeway Drive is available for $3,700,000. USER: That sounds good to me. Can'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '[UNK]' in 'Walnut'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '[UNK] [UNK]' in 'Walnut Creek'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '[UNK] wpoperty in [UNK]' in 'leave.A wpoperty in Walnut'
INFO:simpletransformers.question_answering.question_answering_utils:

INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '[UNK] it please on 7th of [UNK]' in 'No.Make it please on 7th of March.'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '6th . [UNK] that correct ? [UNK] : [UNK] . [UNK] it please on 7th' in '6th.Is that correct? USER: No.Make it please on 7th'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '[UNK] cost $ 2 , 800 and is located at 150 [UNK] [UNK]' in 'options.First cost $2,800 and is located at 150 Sierra Drive.Is'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '[UNK] [UNK] [UNK] on [UNK] 6th . [UNK] that correct ? [UNK] : [UNK] . [UNK] it please on 7th' in 'Affordable Housing Associates on March 6th.Is that correct? USER: No.Make it please on 7th'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '6th will be great . [UNK] : [UNK] sche

INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '[UNK] : [UNK] [UNK] would . [UNK] would like to visit on 8th of [UNK]' in 'USER: Yes I would. I would like to visit on 8th of March.'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '[UNK]' in 'Would'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '[UNK] [UNK] would . [UNK] would like to visit on 8th of [UNK]' in 'Yes I would. I would like to visit on 8th of March.'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '[UNK] .' in 'March.'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '[UNK] would like to visit on 8th' in 'I would like to visit on 8th'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '[UNK] would . [UNK] would like to visit on 8th of [UNK]' in 'I would. I would like to visit on 8th 

INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: 'in [UNK] [UNK]' in 'in San Fran'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '[UNK] and has 2 baths .' in 'Fran and has 2 baths.'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '[UNK] [UNK] and has 2 baths' in 'San Fran and has 2 baths.'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: 'in [UNK]' in 'in San'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '[UNK] can buy that is in [UNK] [UNK]' in 'I can buy that is in San Fran'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '[UNK] and has 2 baths' in 'Fran and has 2 baths.'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '[UNK] : [UNK] need a place [UNK] can buy that is in [UNK] [UNK]' in 'USER: I nee

INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '[UNK] [UNK] on [UNK] 13th , correct ? [UNK] : [UNK]' in 'Carter Terrace on March 13th, correct? USER: No'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '[UNK]' in 'Carter'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '[UNK] 13th , correct ? [UNK] : [UNK] please make it the 4th of this month' in 'March 13th, correct? USER: No please make it the 4th of this month.'
INFO:simpletransformers.question_answering.question_answering_utils:Unable to find text: '13th . [UNK] : [UNK] would like to visit [UNK] [UNK] on [UNK] 13th , correct ? [UNK] : [UNK] please make it the 4th of this month .' in '13th. SYSTEM: You would like to visit Carter Terrace on March 13th, correct? USER: No please make it the 4th of this month.'
INFO:simpletransformers.question_answering.question_answering_model:[{'context': "USER: Get me a house to

In [231]:
# Failure Analysis
def read_dict(filename):
    with open(filename) as f:
        return json.load(f)
def read_json(filename):
    with open(filename) as f:
        return json.load(f)
    



In [270]:
from collections import Counter
def read_results(filename):
    out = read_dict(filename)
    all_slot_num = (len(out['correct_text']) + len(out['similar_text']) + len(out['incorrect_text']))
    slot_acc = len(out['correct_text']) / all_slot_num
    
    correct_turns = set([i.split("-")[0] +"-" + i.split("-")[3] for i in out['correct_text'].keys()])
    incorrect_turns = set([i.split("-")[0] +"-" + i.split("-")[3] for i in list(out['similar_text'].keys()) + list(out['incorrect_text'].keys())])
    join_slot_acc = len(correct_turns.difference(incorrect_turns)) / all_slot_num
    
#   domains
#     correct_domains = Counter([i.split("-")[1].split("_")[0] for i in list(out['correct_text'].keys())])
#     incorrect_domains = Counter([i.split("-")[1].split("_")[0] for i in list(out['similar_text'].keys()) + list(out['incorrect_text'].keys())])
#     for d in sorted(correct_domains):
#         print(correct_domains[d] / (correct_domains[d] + incorrect_domains[d]))
    
#     print(out['correct_text'])

    
    correct_turn_domains = set([i.split("-")[1].split("_")[0] + "-" + i.split("-")[0] +"-" + i.split("-")[3] for i in list(out['correct_text'].keys())])
    incorrect_turn_domains = set([i.split("-")[1].split("_")[0] + "-" + i.split("-")[0] +"-" + i.split("-")[3] for i in list(out['similar_text'].keys()) + list(out['incorrect_text'].keys())])
    join_correct_domains = Counter([i.split("-")[0] for i in correct_turn_domains.difference(incorrect_turn_domains)])
    join_incorrect_domains = Counter([i.split("-")[0] for i in correct_turn_domains.union(incorrect_turn_domains).difference(correct_turn_domains.difference(incorrect_turn_domains))])
#     join_incorrect_domains = Counter([i.split("-")[0] for i in correct_turn_domains.union(incorrect_turn_domains)])
    
    print(len(incorrect_turn_domains))
    print(correct_turn_domains)
#     print(join_incorrect_domains)
    
#     for d in sorted(join_incorrect_domains):
#         print(join_correct_domains[d] / (join_correct_domains[d] + join_incorrect_domains[d]))
        
#   Slots
#     correct_domains = Counter([i.split("-")[2] for i in list(out['correct_text'].keys())])
#     incorrect_domains = Counter([i.split("-")[2] for i in list(out['similar_text'].keys()) + list(out['incorrect_text'].keys())])
#     for d in sorted(correct_domains):
#         print(d)
#         print(correct_domains[d] / (correct_domains[d] + incorrect_domains[d]))

        
    correct_slots = Counter([i.split("-")[2] for i in list(out['correct_text'].keys())])
    incorrect_slots = Counter([i.split("-")[2] for i in list(out['similar_text'].keys()) + list(out['incorrect_text'].keys())])
#     for d in correct_slots:
#         print(d, correct_slots[d] / (correct_slots[d] + incorrect_slots[d]))
        
    return slot_acc, join_slot_acc

print(read_results("out/multiwoz2.0_bert.out"))
# print()
# print(read_results("out/multiwoz2.0_bert_wdc.out"))



287
{'hotel-SNG01784.json-t0', 'restaurant-PMUL4440.json-t1', 'restaurant-PMUL0506.json-t6', 'hotel-PMUL4440.json-t5', 'restaurant-SNG0477.json-t0', 'train-MUL1870.json-t3', 'restaurant-SNG01755.json-t3', 'attraction-MUL2365.json-t0', 'attraction-PMUL4106.json-t1', 'train-PMUL3027.json-t3', 'taxi-PMUL0006.json-t7', 'train-MUL2137.json-t5', 'hotel-MUL2053.json-t0', 'hotel-SNG01551.json-t7', 'restaurant-MUL1202.json-t4', 'taxi-PMUL0320.json-t9', 'restaurant-PMUL4220.json-t1', 'hotel-SNG0768.json-t1', 'train-MUL0389.json-t2', 'hotel-PMUL4247.json-t1', 'train-PMUL3935.json-t0', 'restaurant-MUL0843.json-t3', 'attraction-PMUL4326.json-t3', 'restaurant-PMUL3310.json-t5', 'restaurant-SNG0529.json-t2', 'train-MUL1478.json-t4', 'train-MUL0383.json-t1', 'hotel-PMUL0109.json-t3', 'hotel-SNG01943.json-t2', 'attraction-PMUL2123.json-t1', 'restaurant-SNG0701.json-t0', 'hotel-MUL2148.json-t1', 'hotel-SNG0892.json-t0', 'train-PMUL3247.json-t5', 'hotel-PMUL0076.json-t4', 'train-SNG0263.json-t0', 'train-

In [236]:
out['similar_text']

{'1100000-Hotels_2-where_to-t2-f0-s0': {'truth': 'London',
  'predicted': 'London.',
  'question': 'A popular service for searching and booking houses for short term stay Location of the house'},
 '1100001-Hotels_2-where_to-t2-f0-s0': {'truth': 'Philly',
  'predicted': 'Philly.',
  'question': 'A popular service for searching and booking houses for short term stay Location of the house'},
 '1100002-Hotels_2-where_to-t2-f0-s0': {'truth': 'London',
  'predicted': 'London.',
  'question': 'A popular service for searching and booking houses for short term stay Location of the house'},
 '1100003-Hotels_2-where_to-t2-f0-s0': {'truth': 'Paris',
  'predicted': 'Paris.',
  'question': 'A popular service for searching and booking houses for short term stay Location of the house'},
 '1100004-Hotels_2-where_to-t2-f0-s0': {'truth': 'Sydney',
  'predicted': 'Sydney.',
  'question': 'A popular service for searching and booking houses for short term stay Location of the house'},
 '1100005-Hotels_2-whe

['Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Hotels',
 'Weather',
 'Weather',
 'Weather',
 'Weather',
 'Weather',
 'Weather',
 'Weather',
 'W

In [230]:
join_slot_acc

0.35390593748214183

In [141]:
incorrect_ids = out['incorrect_text'].keys()

In [142]:
def getId2Service(test):
    id2service = {}
    for i in test:
        for j in i['qas']:
            if 'service' in j:
                id2service[j['id']] = simplifyDomainName(j['service'])
    return id2service
id2service = getId2Service(test)

In [143]:
from collections import Counter
def printFreq(l):
    for i in sorted(Counter(l).items(), key=lambda x: -x[1])[:10]:
         print(i[0] +","+ str(i[1]))
printFreq([id2service[i] for i in incorrect_ids])
print()
printFreq([out['incorrect_text'][i]['question'] for i in out['incorrect_text']])

hotel,2678
service,1531
rent car,1258
event,1071
media,368
movie,215
taxi,212
weather,113
bank,59
travel,18

Location of the house,473
Date for the appointment,400
Review rating of the house,396
Number of days in the reservation,335
Address of the house,329
Starting time for event,277
Time of the appointment,264
Name of the dentist,261
Date of rental car pickup,235
Name of the director of the movie,219


In [144]:
out['incorrect_text']

{'17': {'truth': '17 eastern parkway, brooklyn',
  'predicted': 'venue',
  'question': 'Address of event venue'},
 '21': {'truth': 'Murmrr',
  'predicted': 'venue',
  'question': 'Exact venue of event'},
 '27': {'truth': 'Murmrr',
  'predicted': 'venue',
  'question': 'Exact venue of event'},
 '29': {'truth': '17 eastern parkway, brooklyn',
  'predicted': 'venue',
  'question': 'Address of event venue'},
 '45': {'truth': '5:30 pm',
  'predicted': 'time',
  'question': 'Starting time for event'},
 '95': {'truth': '7 pm',
  'predicted': 'time',
  'question': 'Starting time for event'},
 '153': {'truth': '56-15 Northern Boulevard, Woodside',
  'predicted': 'venue',
  'question': 'Address of event venue'},
 '161': {'truth': 'La Boom',
  'predicted': 'venue',
  'question': 'Exact venue of event'},
 '163': {'truth': '56-15 Northern Boulevard, Woodside',
  'predicted': 'venue',
  'question': 'Address of event venue'},
 '169': {'truth': 'La Boom',
  'predicted': 'venue',
  'question': 'Exact v

In [303]:
from transformers import BertTokenizer, BertForQuestionAnswering
import torch

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
model = BertForQuestionAnswering.from_pretrained('bert-base-uncased')

question, text = "Who was Jim Henson?", "Jim Henson was a nice puppet"
input_ids = tokenizer.encode([question, text])
token_type_ids = [0 if i <= input_ids.index(102) else 1 for i in range(len(input_ids))]
start_scores, end_scores = model(torch.tensor([input_ids]), token_type_ids=torch.tensor([token_type_ids]))

all_tokens = tokenizer.convert_ids_to_tokens(input_ids)
answer = ' '.join(all_tokens[torch.argmax(start_scores) : torch.argmax(end_scores)+1])

assert answer == "a nice puppet"

AssertionError: 

In [325]:
from collections import defaultdict
record = dst_train.iloc[0]
dialogue_idx = record.dialogue_id
domains = record.services
dialogue = []

system_transcript = ""
ontology = defaultdict(list)
turn_idx = 0
for i, record in dst_train.iterrows():
    for idx, rec in enumerate(record.turns):

        if rec['speaker'] == "SYSTEM":
            system_transcript = rec['utterance']
        else:
            belief_state = []
            turn_idx = idx
            print(rec['utterance'])
            for frame in rec['frames']:
                for action in frame['actions']:
                    if action['act'] == "INFORM"
                print(frame)
                state = {}
                print(frame['state']['slot_values'])
            print(len(rec['frames']))
            print()
    if i == 10:
        break

I'm looking for some free attractions to check out.
{'actions': [{'act': 'INFORM', 'canonical_values': ['True'], 'slot': 'free_entry', 'values': ['True']}, {'act': 'INFORM_INTENT', 'canonical_values': ['FindAttractions'], 'slot': 'intent', 'values': ['FindAttractions']}], 'service': 'Travel_1', 'slots': [], 'state': {'active_intent': 'FindAttractions', 'requested_slots': [], 'slot_values': {'free_entry': ['True']}}}
1

Something of a place of interest in NYC.
{'actions': [{'act': 'INFORM', 'canonical_values': ['New York'], 'slot': 'location', 'values': ['NYC']}, {'act': 'INFORM', 'canonical_values': ['Tourist Attraction'], 'slot': 'category', 'values': ['Tourist Attraction']}], 'service': 'Travel_1', 'slots': [{'exclusive_end': 39, 'slot': 'location', 'start': 36}], 'state': {'active_intent': 'FindAttractions', 'requested_slots': [], 'slot_values': {'category': ['Tourist Attraction'], 'free_entry': ['True'], 'location': ['NYC']}}}
1

Is it kid-friendly?
{'actions': [{'act': 'REQUEST', 

In [178]:
def generate_wdc_data_for_multiwoz(wdc, filename):
    train_data = []
    ontology = {}
    dialogue_idx = 0
    for idx, grp in wdc.groupby("website"):
        domain = grp.entityType.values[0]
        try:
            transcript = " ".join(grp['value'].tolist())
            belief_state = []
            turn_label = []
            for i, row in grp.iterrows():
#                 slot_name = "%s-%s" % (domain, prop2desc[row['property']].replace("-",""))
                slot_name = "%s-%s" % (domain, "schema "+row['property'])
#                 slot_name = "hotel-typeb"
                ontology[str(slot_name)] = []
                belief_state.append({'slots':[[slot_name, row['value']]], 'act':'inform'})
                turn_label.append([slot_name, row['value']])
                break
            
        except:
            continue
        a ={
                "dialogue_idx": str(dialogue_idx),
                "domains": [
                    domain
                ],
                "dialogue": [
                    {
                        "system_transcript": "",
                        "turn_idx": 0,
                        "belief_state": belief_state,
                        "turn_label": turn_label,
                        "transcript": transcript,
                        "system_acts": [],
                        "domain": domain
                    }
                ]
            }
        
        dialogue_idx += 1
        train_data.append(a)
        
#         break
#     Save as a JSON file
#     train_data = json.dumps(train_data)
    print(json.dumps(ontology))
    os.makedirs('data', exist_ok=True)
    with open('data/multiwoz2.1/%s_dials.json' % filename, 'w') as f:
        json.dump(train_data, f)
    return train_data
x = generate_wdc_data_for_multiwoz(wdc2[:100000], "wdc")
# Train the model with JSON file
# model.train_model('data/wdc.json')

{"attraction-schema telephone": [], "hotel-schema streetAddress": [], "attraction-schema streetAddress": [], "hotel-schema text": [], "attraction-schema articleBody": [], "hotel-schema reviewBody": [], "hotel-schema addressLocality": [], "hotel-schema priceRange": [], "attraction-schema title": [], "attraction-schema value": [], "attraction-schema longitude": [], "attraction-schema reviewBody": [], "attraction-schema postalCode": [], "hotel-schema address": [], "attraction-schema address": [], "hotel-schema articleBody": [], "attraction-schema openingHours": [], "attraction-schema workHours": [], "attraction-schema StartDate": [], "hotel-schema openingHours": [], "attraction-schema latitude": [], "hotel-schema alternateName": [], "attraction-schema faxNumber": [], "attraction-schema contentLocation": [], "attraction-schema creator": [], "hotel-schema postalCode": [], "attraction-schema transcript": [], "attraction-schema addressLocality": [], "attraction-schema actor": [], "hotel-schem

In [165]:
wdc2 = wdc[wdc.entityType.isin(["hotel", "restaurant", "place"])]

In [166]:
wdc2['entityType'] = [i if i != "place" else "attraction" for i in wdc2['entityType']]

/Users/jarana/anaconda3/envs/torch1/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [179]:
import json

In [229]:
def convert_multiwoz_to_sgd(train, filename):
    train_data = []
    for i in range(len(train)):
        dialogue_id = train[i]['dialogue_idx']
        for t in range(len(train[i]['dialogue'])):
            dialog = train[i]['dialogue'][t]
            service = dialog['domain']
            context = dialog['system_transcript'] + " " + dialog['transcript']
            qas = []
            for s, turn in enumerate(dialog['turn_label']):
                slot_name = turn[0]
                value = turn[1]
                if value in context:
                    qas.append({'id': "%s-%s-%s-t%d-f%d-s%d" % (dialogue_id, service, slot_name.replace("-","_"), t, 0, s), 'is_impossible': False, 'question': slot_name, 'answers': [{'text': value, 'answer_start': context.index(value)}]})
            if len(qas) > 0:
                train_data.append({'context': context, 'qas' : qas})

    os.makedirs('data', exist_ok=True)
    with open('data/sgd/%s.json' % ("multiwoz2.1-" + filename), 'w') as f:
        json.dump(train_data, f)
    
train = json.load(open("data/multiwoz2.1/train_dials.json"))
convert_multiwoz_to_sgd(train, "train")
train = json.load(open("data/multiwoz2.1/test_dials.json"))
convert_multiwoz_to_sgd(train, "test")

In [73]:
train = json.load(open("data/multiwoz2.1/train_dials.json"))


In [76]:
len(train)

8420

In [81]:
turns = 0
for i in range(len(train)):
    turns += len(train[i]['dialogue'])

In [82]:
turns

56668